In [1]:
import random
import calendar
import time
import math
import numpy as np

origintime=0
max_policies=10
max_policy_changes=3
#max_policy_length=365*24*3600
max_policy_length=3600
policy_vars=[3,8]
#policy_m_init=11
#policy_sd_init=4.2
policy_m_init=4
policy_sd_init=1.5


baseclaimrate=1.2
claim_rates=[0.1,0.2]
claim_report_m=11
claim_report_sd=3
claim_payment_rate=1.3

payment_m=9
payment_sd=4
payment_time_delay_m=3
payment_time_delay_sd=1.5


max_claims=1
max_periods=3
max_class=3
max_customer_changes=2

#All timelines are calendar
#Sendingtimes are random, but after origintime

class Sample:
    def __init__(self,polnr):
        self.policies(polnr)
        self.customers()
        self.claims()
        self.combine()
        
    def customers(self):
        times=[p["policystarttime"] for p in self.policy]
        self.customer=[]
        self.customer.append({"customer":"cust"+str(self.policy[0]["policy"]),"customertime":self.policy[0]["policystarttime"],"address":"Here"})
        r=random.sample(times,1)[0]
        if r!=times[0]:
             self.customer.append({"customer":"cust"+str(self.policy[0]["policy"]),"customertime":r,"address":"There"})
        
    def policies(self,polnr):
        #Only one policy is made
        self.policy=[]
        policynr=random.randint(1,max_policies)
        if polnr>0:
            policynr=polnr
        lasttime=origintime+random.lognormvariate(policy_m_init,policy_sd_init)
        for _ in range(random.randint(1,max_policy_changes)):
            newtime=random.uniform(lasttime,lasttime+max_policy_length)
            newpolicy={"policy":policynr,"policystarttime":lasttime,"policyendtime":newtime}
            lasttime=newtime
            ci=0
            for i in policy_vars:
                newpolicy[str("pvar"+str(ci))]=random.sample(set(range(i)),1)[0]
                ci=ci+1
            self.policy.append(newpolicy)

    def claims(self):
        self.claim=[]
        self.claimpayment=[]
        times=[p["policystarttime"] for p in self.policy]
        claimpayment=[]
        claimcount=0
        for ci in range(len(self.policy)):
            rate=baseclaimrate
            for i in range(len(policy_vars)):
                rate=rate+claim_rates[i]*self.policy[ci][str("pvar"+str(i))]
            mu=rate*(float(self.policy[ci]["policyendtime"])-float(self.policy[ci]["policystarttime"]))
            mu=mu/max_policy_length
            claimcounts=math.floor(random.expovariate(1/mu))
            lastclaimtime=self.policy[ci]["policystarttime"]
            for c in range(claimcounts):
                claimtime=random.uniform(lastclaimtime,self.policy[ci]["policyendtime"])
                claimreporttime=claimtime+random.lognormvariate(claim_report_m,claim_report_sd)
                lastclaimtime=claimtime
                claimnumber=str(self.policy[0]["policy"])+"_"+str(claimcount)
                self.claim.append({"claimnumber":claimnumber,"claimtime":claimtime,"claimreporttime":claimreporttime,"claimcounter":claimcount})
                claimcount=claimcount+1
                mupayments=claim_payment_rate
                countpayments=math.floor(random.expovariate(1/mupayments))
                #print("countpayments is "+str(countpayments))
                lastpaytime=self.claim[c]["claimreporttime"]
                for pay in range(countpayments):
                    amount=random.lognormvariate(payment_m,payment_sd)
                    paytime=lastpaytime+random.lognormvariate(payment_time_delay_m,payment_time_delay_sd)
                    lastpaytime=paytime
                    self.claimpayment.append({"claimnumber":self.claim[c]["claimnumber"],"claimcounter":self.claim[c]["claimcounter"],"paytime":paytime,"payment":amount})

    def combine(self):
        self.data={"customer":self.customer,"policy":self.policy,"claim":self.claim,"payment":self.claimpayment}

    def reportdata(self,a):
        #create random delays for all stuff, then combine
        if isinstance(a,dict):
            for k in a.keys():
                print(k)

    def recordsinint(self,fra,til):
        newcustomer=[c for c in self.customer if c["customertime"]<til and c["customertime"]>=fra]
        newpolicy=[c for c in self.policy if c["policystarttime"]<til and c["policystarttime"]>=fra]
        newclaim=[c for c in self.claim if c["claimreporttime"]<til and c["claimreporttime"]>=fra]
        newclaimpayment=[c for c in self.claimpayment if c["paytime"]<til and c["paytime"]>=fra]
        self.newdata={"customer":newcustomer,"policy":newpolicy,"claim":newclaim,"payment":newclaimpayment}
        
    def print(self):
        #print(self.customer)
        #print("\n")
        #print(self.policy)
        #print("\n")
        #print(self.claim)
        #print("\n")
        #print(self.claimpayment)
        print(self.data)
        



In [2]:
!pip install kafka-python

In [4]:
data=[Sample(i) for i in range(100000)]
data_customer=[d.customer for d in data]
data_policy=[d.policy for d in data]
data_claim=[d.claim for d in data]
data_claimpayment=[d.claimpayment for d in data]



In [ ]:
for d in data_claim:
    print(d)

In [ ]:
for d in data:
    print(d.data)

In [3]:
from kafka import KafkaProducer
from kafka.errors import KafkaError
import json



In [5]:
producer = KafkaProducer(value_serializer=lambda m: json.dumps(m).encode('ascii'),bootstrap_servers=['10.101.12.4:9092'])

for d in data_customer:
    producer.send('customer', d[0])

for d in data_policy:
    producer.send('policy', d[0])

for d in data_claim:
    if len(d)>0:
        producer.send('claim', d[0])

for d in data_claimpayment:
    if len(d)>0:
        producer.send('claimpayment', d[0])

for d in data:
    if len(d.data)>0:
        producer.send('total', d.data)

producer.flush()

In [15]:
producer = KafkaProducer(value_serializer=lambda m: json.dumps(m).encode('ascii'),bootstrap_servers=['10.101.12.4:9092'])

for i in range(10):
    print("Sample nr "+str(i))
    d=Sample(i)
    data_customer=d.customer[0]
    data_policy=d.policy[0]
    data_claim=d.claim
    data_claimpayment=d.claimpayment
    producer.send('customer', data_customer)
    print(data_customer)
    producer.send('policy', data_policy)
    print(data_policy)
    if len(data_claim)>0:
        #print("claim")
        #print(data_claim[0])
        producer.send('claim', data_claim[0])
    if len(data_claimpayment)>0:
        #print("payment")
        #print(data_claimpayment[0])
        producer.send('claimpayment', data_claimpayment[0])
    print("Total")
    producer.send('total', d.data)
    producer.flush()



Sample nr 0
{'customer': 'cust9', 'customertime': 34.713983525946745, 'address': 'Here'}
{'policy': 9, 'pvar0': 1, 'policyendtime': 2885.9793433101654, 'pvar1': 4, 'policystarttime': 34.713983525946745}
Total
Sample nr 1
{'customer': 'cust1', 'customertime': 643.6708599763815, 'address': 'Here'}
{'policy': 1, 'pvar0': 1, 'policyendtime': 1614.9243734963343, 'pvar1': 5, 'policystarttime': 643.6708599763815}
Total
Sample nr 2
{'customer': 'cust2', 'customertime': 3.9712739259210923, 'address': 'Here'}
{'policy': 2, 'pvar0': 2, 'policyendtime': 479.9023596096196, 'pvar1': 3, 'policystarttime': 3.9712739259210923}
Total
Sample nr 3
{'customer': 'cust3', 'customertime': 92.48265844394534, 'address': 'Here'}
{'policy': 3, 'pvar0': 0, 'policyendtime': 1636.9481942851194, 'pvar1': 4, 'policystarttime': 92.48265844394534}
Total
Sample nr 4
{'customer': 'cust4', 'customertime': 36.74390895702417, 'address': 'Here'}
{'policy': 4, 'pvar0': 1, 'policyendtime': 499.6040622770967, 'pvar1': 5, 'policy

In [7]:
from kafka import KafkaConsumer
consumer = KafkaConsumer('total',bootstrap_servers=['10.101.12.4:9092'],auto_offset_reset='earliest')
consumer.subscribe(['total'])
for message in consumer:
    print (message)


ConsumerRecord(topic='total', partition=0, offset=0, timestamp=1511953092444, timestamp_type=0, key=None, value=b'{"payment": [], "claim": [], "policy": [{"policystarttime": 85.02628534095223, "policyendtime": 691.391276844762, "policy": 1, "pvar0": 2, "pvar1": 0}, {"policystarttime": 691.391276844762, "policyendtime": 1862.1236265028729, "policy": 1, "pvar0": 1, "pvar1": 4}], "customer": [{"customertime": 85.02628534095223, "address": "Here", "customer": "cust1"}]}', checksum=1505741123, serialized_key_size=-1, serialized_value_size=356)
ConsumerRecord(topic='total', partition=0, offset=1, timestamp=1511953092444, timestamp_type=0, key=None, value=b'{"payment": [], "claim": [], "policy": [{"policystarttime": 7.678510018141431, "policyendtime": 873.0326599617194, "policy": 1, "pvar0": 1, "pvar1": 1}], "customer": [{"customertime": 7.678510018141431, "address": "Here", "customer": "cust1"}]}', checksum=-313513731, serialized_key_size=-1, serialized_value_size=244)
ConsumerRecord(topic='

KeyboardInterrupt: 

In [ ]:
from kafka import KafkaConsumer
consumer = KafkaConsumer('pertest',bootstrap_servers=['10.101.12.4:9092'],auto_offset_reset='earliest')
consumer.subscribe(['claim'])
for message in consumer:
    print (message)

